In [100]:
import pandas as pd
import numpy as np
import binascii
from keras.utils import np_utils
from sklearn.preprocessing import LabelEncoder, MinMaxScaler

print("----------------------DATA check-----------------------------------------")
# 파일읽기

# gcc5_0_32_abc
gcc5_0_32a = pd.read_csv("gcc5/gcc5_0_32a.csv")
gcc5_0_32b = pd.read_csv('gcc5/gcc5_0_32b.csv')
gcc5_0_32c = pd.read_csv('gcc5/gcc5_0_32c.csv')

# gcc5_1_32_abc
gcc5_1_32a = pd.read_csv("gcc5/gcc5_1_32a.csv")
gcc5_1_32b = pd.read_csv('gcc5/gcc5_1_32b.csv')
gcc5_1_32c = pd.read_csv('gcc5/gcc5_1_32c.csv')

# gcc5_2_32_abc
gcc5_2_32a = pd.read_csv("gcc5/gcc5_2_32a.csv")
gcc5_2_32b = pd.read_csv('gcc5/gcc5_2_32b.csv')
gcc5_2_32c = pd.read_csv('gcc5/gcc5_2_32c.csv')

# gcc5_0_32_ab
gcc5_0_32ab = pd.concat([gcc5_0_32a, gcc5_0_32b])
gcc5_0_32c

# gcc5_1_32_c
gcc5_1_32ab = pd.concat([gcc5_1_32a, gcc5_1_32b])
gcc5_1_32c

# gcc5_2_32_c
gcc5_2_32ab = pd.concat([gcc5_2_32a, gcc5_2_32b])
gcc5_2_32c

# 형태 출력
print(gcc5_0_32ab.shape, gcc5_1_32ab.shape, gcc5_2_32ab.shape) # train
print(gcc5_0_32c.shape, gcc5_1_32c.shape, gcc5_2_32c.shape) # test

----------------------DATA check-----------------------------------------
(1791093, 2) (1790893, 2) (1791140, 2)
(895554, 2) (87633, 2) (166319, 2)


In [101]:
# 16진수 256개 종류가 있어서 pd.get_dummies 사용 가능.
print(len(gcc5_0_32ab['bin'].unique()))
print(len(gcc5_1_32ab['bin'].unique()))
print(len(gcc5_2_32ab['bin'].unique()))

256
256
256


In [102]:
print("------------------------- one hot encoding ----------------------------")

# gcc 최적화버전 1,2,3 one hot encoding
# gcc5_0_32ab_onehot, gcc5_1_32ab_onehot, gcc5_2_32ab_onehot
gcc5_0_32ab_onehot = pd.get_dummies(gcc5_0_32ab)
gcc5_1_32ab_onehot = pd.get_dummies(gcc5_1_32ab)
gcc5_2_32ab_onehot = pd.get_dummies(gcc5_2_32ab)

# test 셋들 
gcc5_0_32c_onehot = pd.get_dummies(gcc5_0_32c)
gcc5_1_32c_onehot = pd.get_dummies(gcc5_1_32c)
gcc5_2_32c_onehot = pd.get_dummies(gcc5_2_32c)
print('원핫인코딩완료')

print(gcc5_0_32ab_onehot.shape, gcc5_1_32ab_onehot.shape, gcc5_2_32ab_onehot.shape)
print(gcc5_0_32c_onehot.shape, gcc5_1_32c_onehot.shape, gcc5_2_32c_onehot.shape)

------------------------- one hot encoding ----------------------------
원핫인코딩완료
(1791093, 257) (1790893, 257) (1791140, 257)
(895554, 257) (87633, 257) (166319, 257)


In [112]:
gcc5_0_32ab_onehot

bin_0  bin_0a  bin_0b  bin_0c  bin_0d  bin_0e  bin_0f  bin_1  bin_10  \
0           0       0       0       0       0       0       0      0       0   
1           0       0       0       0       0       0       0      0       0   
2           0       0       0       0       0       0       0      0       0   
3           0       0       0       0       0       0       0      0       0   
4           0       0       0       0       0       0       0      0       0   
...       ...     ...     ...     ...     ...     ...     ...    ...     ...   
895539      1       0       0       0       0       0       0      0       0   
895540      1       0       0       0       0       0       0      0       0   
895541      1       0       0       0       0       0       0      0       0   
895542      1       0       0       0       0       0       0      0       0   
895543      0       0       0       0       0       0       0      0       0   

        bin_11  ...  bin_f6  bin_f7  bin_f8  bin_f9  bin_fa  bin_fb  bin_fc  \
0            0  ...       0       0       0       0       0       0       0   
1            0  ...       0       0       0       0       0       0       0   
2            0  ...       0       0       0       0       0       0       0   
3            0  ...       0       0       0       0       0       0       0   
4            0  ...       0       0       0       0       0       0       0   
...        ...  ...     ...     ...     ...     ...     ...     ...     ...   
895539       0  ...       0       0       0       0       0       0       0   
895540       0  ...       0       0       0       0       0       0       0   
895541       0  ...       0       0       0       0       0       0       0   
895542       0  ...       0       0       0       0       0       0       0   
895543       0  ...       0       0       0       0       0       0       0   

        bin_fd  bin_fe  bin_ff  
0            0       0       0  
1            0       0       0  
2            0       0       0  
3            0       0       0  
4            0       0       0  
...        ...     ...     ...  
895539       0       0       0  
895540       0       0       0  
895541       0       0       0  
895542       0       0       0  
895543       0       0       0  

[1791093 rows x 256 columns]

In [103]:
####### (1) 
from keras.models import Sequential
from keras.layers import SimpleRNN

import warnings
warnings.filterwarnings(action='ignore')

import numpy as np
import pandas as pd

####### (1)
# 정답 데이터 1, 0 비율 확인  ==> 1이 함수의 갯수를 뜻함
print(gcc5_0_32ab_onehot['label'].value_counts())
print(gcc5_1_32ab_onehot['label'].value_counts())
print(gcc5_2_32ab_onehot['label'].value_counts())

print(gcc5_0_32c_onehot['label'].value_counts())
print(gcc5_1_32c_onehot['label'].value_counts())
print(gcc5_2_32c_onehot['label'].value_counts())

0    1788127
1       2966
Name: label, dtype: int64
0    1787727
1       3166
Name: label, dtype: int64
0    1788221
1       2919
Name: label, dtype: int64
0    894078
1      1476
Name: label, dtype: int64
0    87452
1      181
Name: label, dtype: int64
0    165957
1       362
Name: label, dtype: int64


In [104]:
# train 셋들 label 제거
del gcc5_0_32ab_onehot['label']
del gcc5_1_32ab_onehot['label']
del gcc5_2_32ab_onehot['label']

# test 셋들 label 제거
del gcc5_0_32c_onehot['label']
del gcc5_1_32c_onehot['label']
del gcc5_2_32c_onehot['label']
print(gcc5_0_32ab_onehot.shape, gcc5_1_32ab_onehot.shape, gcc5_2_32ab_onehot.shape)
print(gcc5_0_32c_onehot.shape, gcc5_1_32c_onehot.shape, gcc5_2_32c_onehot.shape)

(1791093, 256) (1790893, 256) (1791140, 256)
(895554, 256) (87633, 256) (166319, 256)


In [105]:
####### (3) 

############## gcc5_0
# 훈련데이터 / 테스트 데이터 / gcc5_0_32ab
x_train_gcc_0_32ab = gcc5_0_32ab_onehot.to_numpy()
x_test_gcc_0_32c = gcc5_0_32c_onehot.to_numpy()

# 테스트 라벨 / y_train, y_test / gcc5_0_32_ab
y_train_gcc_0_32ab = gcc5_0_32ab['label'].to_numpy()
y_test_gcc_0_32c = gcc5_0_32c['label'].to_numpy()

print('gcc_5_0 최적화 0 완료')

############## gcc5_1
# 훈련데이터 / 테스트 데이터 / gcc5_1_32ab
x_train_gcc_1_32ab = gcc5_1_32ab_onehot.to_numpy()
x_test_gcc_1_32c = gcc5_1_32c_onehot.to_numpy()

# 테스트 라벨 / y_train, y_test / gcc5_1_32_ab
y_train_gcc_1_32ab = gcc5_1_32ab['label'].to_numpy()
y_test_gcc_1_32c = gcc5_1_32c['label'].to_numpy()

print('gcc_5_1 최적화 1 완료')

############## gcc5_2

# 훈련데이터 / 테스트 데이터 / gcc5_2_32ab
x_train_gcc_2_32ab = gcc5_2_32ab_onehot.to_numpy()
x_test_gcc_2_32c = gcc5_2_32c_onehot.to_numpy()

# 테스트 라벨 / y_train, y_test / gcc5_2_32_ab
y_train_gcc_2_32ab = gcc5_2_32ab['label'].to_numpy()
y_test_gcc_2_32c = gcc5_2_32c['label'].to_numpy()

print('gcc_5_2 최적화 2 완료')

print('-----------------------------------------------')
print(x_train_gcc_0_32ab.shape, x_train_gcc_1_32ab.shape, x_train_gcc_2_32ab.shape)
print(x_test_gcc_0_32c.shape, x_test_gcc_1_32c.shape, x_test_gcc_2_32c.shape)

print(y_train_gcc_0_32ab.shape, y_train_gcc_1_32ab.shape, y_train_gcc_2_32ab.shape)
print(y_test_gcc_0_32c.shape, y_test_gcc_1_32c.shape, y_test_gcc_2_32c.shape)

gcc_5_0 최적화 0 완료
gcc_5_1 최적화 1 완료
gcc_5_2 최적화 2 완료
-----------------------------------------------
(1791093, 256) (1790893, 256) (1791140, 256)
(895554, 256) (87633, 256) (166319, 256)
(1791093,) (1790893,) (1791140,)
(895554,) (87633,) (166319,)


In [106]:
####### (4) reshape
# (605, 1, 256)

#### 특징변수들 train, test

## gcc_0_32ab / gcc_0_32c
x_train_gcc_0_32ab = x_train_gcc_0_32ab.reshape(x_train_gcc_0_32ab.shape[0], 1, x_train_gcc_0_32ab.shape[1])
x_test_gcc_0_32c = x_test_gcc_0_32c.reshape(x_test_gcc_0_32c.shape[0], 1, x_test_gcc_0_32c.shape[1])

## gcc_1_32ab / gcc_1_32c
x_train_gcc_1_32ab = x_train_gcc_1_32ab.reshape(x_train_gcc_1_32ab.shape[0], 1, x_train_gcc_1_32ab.shape[1])
x_test_gcc_1_32c = x_test_gcc_1_32c.reshape(x_test_gcc_1_32c.shape[0], 1, x_test_gcc_1_32c.shape[1])

## gcc_2_32ab / gcc_2_32c
x_train_gcc_2_32ab = x_train_gcc_2_32ab.reshape(x_train_gcc_2_32ab.shape[0], 1, x_train_gcc_2_32ab.shape[1])
x_test_gcc_2_32c = x_test_gcc_2_32c.reshape(x_test_gcc_2_32c.shape[0], 1, x_test_gcc_2_32c.shape[1])

################################################################################################################

## 목적변수 라벨들 train, test 
y_train_gcc_0_32ab = y_train_gcc_0_32ab.reshape(y_train_gcc_0_32ab.shape[0], 1, 1)
y_test_gcc_0_32c = y_test_gcc_0_32c.reshape(y_test_gcc_0_32c.shape[0], 1, 1)

y_train_gcc_1_32ab = y_train_gcc_1_32ab.reshape(y_train_gcc_1_32ab.shape[0], 1, 1)
y_test_gcc_1_32c = y_test_gcc_1_32c.reshape(y_test_gcc_1_32c.shape[0], 1, 1)

y_train_gcc_2_32ab = y_train_gcc_2_32ab.reshape(y_train_gcc_2_32ab.shape[0], 1, 1)
y_test_gcc_2_32c = y_test_gcc_2_32c.reshape(y_test_gcc_2_32c.shape[0], 1, 1)

################################################################################################################

print(x_train_gcc_0_32ab.shape, x_train_gcc_1_32ab.shape, x_train_gcc_2_32ab.shape)
print(x_test_gcc_0_32c.shape, x_test_gcc_1_32c.shape, x_test_gcc_2_32c.shape)

print(y_train_gcc_0_32ab.shape, y_train_gcc_1_32ab.shape, y_train_gcc_2_32ab.shape)
print(y_test_gcc_0_32c.shape, y_test_gcc_1_32c.shape, y_test_gcc_2_32c.shape)

(1791093, 1, 256) (1790893, 1, 256) (1791140, 1, 256)
(895554, 1, 256) (87633, 1, 256) (166319, 1, 256)
(1791093, 1, 1) (1790893, 1, 1) (1791140, 1, 1)
(895554, 1, 1) (87633, 1, 1) (166319, 1, 1)


In [110]:
############ case 1 -> x_train_gcc_0_32ab / x_train_gcc_0_32c

from keras.models import Model
from keras.layers import Input, Dense, LSTM
from keras.layers import Bidirectional, TimeDistributed
import numpy as np

print(x_train_gcc_0_32ab.shape, y_train_gcc_0_32ab.shape)

# batch_shape => None, 1, 256 뜻 행 batch 크기 안정하고, 1은 열이 1개, 256은 열안의 항목이 256개 
xInput = Input(batch_shape=(None, 1, 256)) # 
xBiLstm = Bidirectional(LSTM(16, return_sequences=True), merge_mode = 'concat')(xInput)
xOutput = TimeDistributed(Dense(1, activation ='sigmoid'))(xBiLstm) # 각 스텝에서 cost가 전송되고, 오류가 다음 step으로 전송됨.


model1 = Model(xInput, xOutput)
model1.compile(loss='binary_crossentropy', optimizer='rmsprop', metrics=['accuracy'])
print(model1.summary())

print('======Training stage======')

# 학습
from keras.callbacks import EarlyStopping
early_stopping = EarlyStopping(patience = 3) # 조기종료 콜백함수 정의

model1.fit(x_train_gcc_0_32ab, y_train_gcc_0_32ab,
          batch_size = 32, #2,
          #validation_split=0.2,
          epochs=3,
          callbacks=[early_stopping])
print('학습완료')

(1791093, 1, 256) (1791093, 1, 1)
Model: "model_7"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_7 (InputLayer)         (None, 1, 256)            0         
_________________________________________________________________
bidirectional_7 (Bidirection (None, 1, 32)             34944     
_________________________________________________________________
time_distributed_7 (TimeDist (None, 1, 1)              33        
Total params: 34,977
Trainable params: 34,977
Non-trainable params: 0
_________________________________________________________________
None
======Training stage======
Epoch 1/3
1791093/1791093 [==============================] - 194s 108us/step - loss: 0.0066 - accuracy: 0.9983
Epoch 2/3
1791093/1791093 [==============================] - 190s 106us/step - loss: 0.0047 - accuracy: 0.9983
Epoch 3/3
1791093/1791093 [==============================] - 176s 98us/step - loss: 0.0047 - accu

In [111]:
score, acc = model1.evaluate(x_test_gcc_0_32c, y_test_gcc_0_32c)
print('Test performance: accuracy={0}, loss={1}'.format(acc, score))

pr1 = model1.predict(x_test_gcc_0_32c)
print(pr1.shape)
pr1

895554/895554 [==============================] - 34s 38us/step
Test performance: accuracy=0.9983518719673157, loss=0.004724964506626009
(895554, 1, 1)


array([[[0.0000000e+00]],

       [[0.0000000e+00]],

       [[0.0000000e+00]],

       ...,

       [[0.0000000e+00]],

       [[2.4975057e-08]],

       [[1.5595377e-07]]], dtype=float32)

In [31]:
############ case 2 -> x_train_gcc_1_32ab / x_train_gcc_1_32c

from keras.models import Model
from keras.layers import Input, Dense, LSTM
from keras.layers import Bidirectional, TimeDistributed
import numpy as np

print(x_train_gcc_1_32ab.shape, y_train_gcc_1_32ab.shape)

# batch_shape => None, 1, 256 뜻 행 batch 크기 안정하고, 1은 열이 1개, 256은 열안의 항목이 256개 
xInput = Input(batch_shape=(None, 1, 256)) # 
xBiLstm = Bidirectional(LSTM(16, return_sequences=True), merge_mode = 'concat')(xInput)
xOutput = TimeDistributed(Dense(1, activation ='sigmoid'))(xBiLstm) # 각 스텝에서 cost가 전송되고, 오류가 다음 step으로 전송됨.

model2 = Model(xInput, xOutput)
model2.compile(loss='binary_crossentropy', optimizer='rmsprop', metrics=['accuracy'])
print(model2.summary())

print('======Training stage======')

# 학습
from keras.callbacks import EarlyStopping
early_stopping = EarlyStopping(patience = 3) # 조기종료 콜백함수 정의

model2.fit(x_train_gcc_1_32ab, y_train_gcc_1_32ab,
          batch_size = 32, #2,
          #validation_split=0.2,
          epochs=3,
          callbacks=[early_stopping])
print('학습완료')

(1790893, 1, 256) (1790893, 1, 1)
Model: "model_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         (None, 1, 256)            0         
_________________________________________________________________
bidirectional_3 (Bidirection (None, 1, 32)             34944     
_________________________________________________________________
time_distributed_3 (TimeDist (None, 1, 1)              33        
Total params: 34,977
Trainable params: 34,977
Non-trainable params: 0
_________________________________________________________________
None
======Training stage======
Epoch 1/3
1790893/1790893 [==============================] - 151s 84us/step - loss: 0.0149 - accuracy: 0.9982
Epoch 2/3
1790893/1790893 [==============================] - 155s 87us/step - loss: 0.0132 - accuracy: 0.9982
Epoch 3/3
1790893/1790893 [==============================] - 159s 89us/step - loss: 0.0133 - accura

In [32]:
############ case 2 -> x_train_gcc_1_32ab / x_train_gcc_1_32c

score, acc = model2.evaluate(x_test_gcc_1_32c, y_test_gcc_1_32c)
print('Test performance: accuracy={0}, loss={1}'.format(acc, score))

pr2 = model2.predict(x_test_gcc_1_32c)
print(pr2.shape)
pr2

87633/87633 [==============================] - 2s 28us/step
Test performance: accuracy=0.9979345798492432, loss=0.018710660961249483
(87633, 1, 1)


array([[[4.0352345e-05]],

       [[4.0352345e-05]],

       [[4.0352345e-05]],

       ...,

       [[2.9236078e-04]],

       [[4.9620867e-05]],

       [[4.2899268e-05]]], dtype=float32)

In [115]:
############ case 3 -> x_train_gcc_2_32ab / x_train_gcc_2_32c

from keras.models import Model
from keras.layers import Input, Dense, LSTM
from keras.layers import Bidirectional, TimeDistributed
import numpy as np

print(x_train_gcc_2_32ab.shape, y_train_gcc_2_32ab.shape)

# batch_shape => None, 1, 256 뜻 행 batch 크기 안정하고, 1은 열이 1개, 256은 열안의 항목이 256개 
xInput = Input(batch_shape=(None, 1, 256)) # 
xBiLstm = Bidirectional(LSTM(16, return_sequences=True), merge_mode = 'concat')(xInput)
xOutput = TimeDistributed(Dense(1, activation ='sigmoid'))(xBiLstm) # 각 스텝에서 cost가 전송되고, 오류가 다음 step으로 전송됨.

model3 = Model(xInput, xOutput)
model3.compile(loss='binary_crossentropy', optimizer='rmsprop', metrics=['accuracy'])
print(model3.summary())

print('======Training stage======')

# 학습
from keras.callbacks import EarlyStopping
early_stopping = EarlyStopping(patience = 3) # 조기종료 콜백함수 정의

model3.fit(x_train_gcc_2_32ab, y_train_gcc_2_32ab,
          batch_size = 32, #2,
          #validation_split=0.2,
          epochs=3,
          callbacks=[early_stopping])
print('학습완료')

(1791140, 1, 256) (1791140, 1, 1)
Model: "model_9"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_9 (InputLayer)         (None, 1, 256)            0         
_________________________________________________________________
bidirectional_9 (Bidirection (None, 1, 32)             34944     
_________________________________________________________________
time_distributed_9 (TimeDist (None, 1, 1)              33        
Total params: 34,977
Trainable params: 34,977
Non-trainable params: 0
_________________________________________________________________
None
======Training stage======
Epoch 1/3
1791140/1791140 [==============================] - 194s 108us/step - loss: 0.0146 - accuracy: 0.9983
Epoch 2/3
1791140/1791140 [==============================] - 199s 111us/step - loss: 0.0127 - accuracy: 0.9984
Epoch 3/3
1791140/1791140 [==============================] - 263s 147us/step - loss: 0.0129 - acc

In [116]:
############ case 3 -> x_train_gcc_2_32ab / x_train_gcc_2_32c

score, acc = model3.evaluate(x_test_gcc_2_32c, y_test_gcc_2_32c)
print('Test performance: accuracy={0}, loss={1}'.format(acc, score))

pr3 = model3.predict(x_test_gcc_2_32c)
print(pr3.shape)
print(pr3)

166319/166319 [==============================] - 12s 72us/step
Test performance: accuracy=0.9978234767913818, loss=0.015393858152240297
(166319, 1, 1)
[[[0.00092676]]

 [[0.00091925]]

 [[0.00118712]]

 ...

 [[0.00227382]]

 [[0.00102369]]

 [[0.00094606]]]


In [121]:
ls = np.array(pr1).flatten().tolist()
ls3 = np.array(pr3).flatten().tolist()

for i in ls+ls3:
    if i >= 0.5:
        print(i)
print('없음')

없음


In [122]:

y_test = np.array(y_test_gcc_2_32c).flatten().tolist()
print(type(y_test))

pre = np.array(pr3).flatten().tolist()
print(type(pre))

print(len(pre), len(y_test))
for i in range(0, len(pre)):
    print(i, pre[i])

<class 'list'>
<class 'list'>
166319 166319
0 0.0009267628192901611
1 0.0009192526340484619
2 0.0011871159076690674
3 0.0010634660720825195
4 0.0008993446826934814
5 0.0008993446826934814
6 0.0008993446826934814
7 0.0008993446826934814
8 0.0009101927280426025
9 0.0009204447269439697
10 0.0012845396995544434
11 0.0009267628192901611
12 0.0008993446826934814
13 0.0008993446826934814
14 0.0009151697158813477
15 0.0009575486183166504
16 0.0008993446826934814
17 0.0008993446826934814
18 0.0008993446826934814
19 0.0008993446826934814
20 0.0009210705757141113
21 0.0010001063346862793
22 0.000937730073928833
23 0.0009267628192901611
24 0.0009532570838928223
25 0.000945746898651123
26 0.0010260939598083496
27 0.0009632706642150879
28 0.0008993446826934814
29 0.0008993446826934814
30 0.0008993446826934814
31 0.0008993446826934814
32 0.0010001063346862793
33 0.0009656548500061035
34 0.0009154975414276123
35 0.0009101927280426025
36 0.0009204447269439697
37 0.0010972917079925537
38 0.0009510815143

914 0.0008993446826934814
915 0.0008993446826934814
916 0.0009381771087646484
917 0.0013010203838348389
918 0.0009655654430389404
919 0.0009049177169799805
920 0.0009049177169799805
921 0.0009827613830566406
922 0.0013911128044128418
923 0.001308351755142212
924 0.0009532570838928223
925 0.0009152591228485107
926 0.0010634660720825195
927 0.0008993446826934814
928 0.0008993446826934814
929 0.0008993446826934814
930 0.0008993446826934814
931 0.0009381771087646484
932 0.001073598861694336
933 0.0010085999965667725
934 0.0009049177169799805
935 0.0009049177169799805
936 0.0009827613830566406
937 0.0009362697601318359
938 0.001308351755142212
939 0.0009532570838928223
940 0.0009152591228485107
941 0.0010634660720825195
942 0.0008993446826934814
943 0.0008993446826934814
944 0.0008993446826934814
945 0.0008993446826934814
946 0.0009381771087646484
947 0.0010766088962554932
948 0.0010085999965667725
949 0.0009049177169799805
950 0.0009049177169799805
951 0.0009532570838928223
952 0.000915259

1905 0.0009049177169799805
1906 0.0009532570838928223
1907 0.0009151697158813477
1908 0.0009510815143585205
1909 0.000912010669708252
1910 0.0009532570838928223
1911 0.000972449779510498
1912 0.001132190227508545
1913 0.0009101927280426025
1914 0.0009204447269439697
1915 0.001052558422088623
1916 0.0009154975414276123
1917 0.0008993446826934814
1918 0.0008993446826934814
1919 0.000928729772567749
1920 0.000972449779510498
1921 0.0010891854763031006
1922 0.0009101927280426025
1923 0.0009204447269439697
1924 0.0013140439987182617
1925 0.0009154975414276123
1926 0.0008993446826934814
1927 0.0008993446826934814
1928 0.0009192526340484619
1929 0.0011871159076690674
1930 0.0009192526340484619
1931 0.000912010669708252
1932 0.0009475648403167725
1933 0.0009287893772125244
1934 0.0009101927280426025
1935 0.0009582638740539551
1936 0.0010008811950683594
1937 0.0009287893772125244
1938 0.00090751051902771
1939 0.001011669635772705
1940 0.0009381771087646484
1941 0.0014424622058868408
1942 0.0010

2905 0.0009575486183166504
2906 0.0008993446826934814
2907 0.0008993446826934814
2908 0.0008993446826934814
2909 0.0008993446826934814
2910 0.0009362697601318359
2911 0.0009048581123352051
2912 0.000977158546447754
2913 0.0009268224239349365
2914 0.0008993446826934814
2915 0.0008993446826934814
2916 0.0008993446826934814
2917 0.0009157061576843262
2918 0.0008993446826934814
2919 0.0008993446826934814
2920 0.0008993446826934814
2921 0.0008993446826934814
2922 0.0009532570838928223
2923 0.00090751051902771
2924 0.0010787546634674072
2925 0.0009532570838928223
2926 0.00090751051902771
2927 0.000945746898651123
2928 0.0009362697601318359
2929 0.0009224414825439453
2930 0.0009157061576843262
2931 0.0008993446826934814
2932 0.0008993446826934814
2933 0.0008993446826934814
2934 0.0008993446826934814
2935 0.0009532570838928223
2936 0.0009151697158813477
2937 0.0010260939598083496
2938 0.0009681880474090576
2939 0.0009532570838928223
2940 0.0009274482727050781
2941 0.001011669635772705
2942 0.0

3958 0.0009274482727050781
3959 0.0009224414825439453
3960 0.001144707202911377
3961 0.0009532570838928223
3962 0.000972449779510498
3963 0.0009157061576843262
3964 0.0009101927280426025
3965 0.0009210705757141113
3966 0.0009192526340484619
3967 0.0009655654430389404
3968 0.0009049177169799805
3969 0.0009049177169799805
3970 0.0009607374668121338
3971 0.0010634660720825195
3972 0.0008993446826934814
3973 0.0008993446826934814
3974 0.0008993446826934814
3975 0.0008993446826934814
3976 0.0009603798389434814
3977 0.0009381771087646484
3978 0.000957876443862915
3979 0.0009655654430389404
3980 0.0009049177169799805
3981 0.0009049177169799805
3982 0.000990837812423706
3983 0.0009532570838928223
3984 0.00090751051902771
3985 0.0010367333889007568
3986 0.0009157061576843262
3987 0.0008993446826934814
3988 0.0008993446826934814
3989 0.0008993446826934814
3990 0.0008993446826934814
3991 0.0009532570838928223
3992 0.00090751051902771
3993 0.001963675022125244
3994 0.0010323822498321533
3995 0.000

...

162384 0.0010323822498321533
162385 0.0009154975414276123
162386 0.0008993446826934814
162387 0.0008993446826934814
162388 0.00090751051902771
162389 0.001149982213973999
162390 0.0009532570838928223
162391 0.00090751051902771
162392 0.0010303854942321777
162393 0.0009157061576843262
162394 0.0011302530765533447
162395 0.0010367333889007568
162396 0.0009049177169799805
162397 0.0009049177169799805
162398 0.0009532570838928223
162399 0.0009151697158813477
162400 0.0009192526340484619
162401 0.000912010669708252
162402 0.0011405646800994873
162403 0.0010811984539031982
162404 0.0009532570838928223
162405 0.0012641549110412598
162406 0.0010490715503692627
162407 0.0010442137718200684
162408 0.0009686946868896484
162409 0.0008993446826934814
162410 0.0008993446826934814
162411 0.0008993446826934814
162412 0.0009101927280426025
162413 0.0009210705757141113
162414 0.001476198434829712
162415 0.0009154975414276123
162416 0.0008993446826934814
162417 0.0008993446826934814
162418 0.000953257083

163216 0.0008993446826934814
163217 0.0008993446826934814
163218 0.0008993446826934814
163219 0.0008993446826934814
163220 0.0013188719749450684
163221 0.0009362697601318359
163222 0.0010891854763031006
163223 0.0009362697601318359
163224 0.0010163187980651855
163225 0.0009532570838928223
163226 0.00090751051902771
163227 0.0010502338409423828
163228 0.0009532570838928223
163229 0.001054316759109497
163230 0.000945746898651123
163231 0.0010556280612945557
163232 0.0009154975414276123
163233 0.0008993446826934814
163234 0.0008993446826934814
163235 0.0009157061576843262
163236 0.0008993446826934814
163237 0.0008993446826934814
163238 0.0008993446826934814
163239 0.0008993446826934814
163240 0.0009532570838928223
163241 0.0009210705757141113
163242 0.0009224414825439453
163243 0.000937730073928833
163244 0.0010265111923217773
163245 0.0009532570838928223
163246 0.0009151697158813477
163247 0.0010878443717956543
163248 0.0009681880474090576
163249 0.0009532570838928223
163250 0.0009210705

164090 0.0010879337787628174
164091 0.0010008811950683594
164092 0.0009532570838928223
164093 0.0009152591228485107
164094 0.0009208917617797852
164095 0.0017731189727783203
164096 0.0009876787662506104
164097 0.0009532570838928223
164098 0.00090751051902771
164099 0.0009208917617797852
164100 0.000912010669708252
164101 0.0009267628192901611
164102 0.0010038018226623535
164103 0.0009362697601318359
164104 0.0009101927280426025
164105 0.0009289085865020752
164106 0.000957876443862915
164107 0.0008993446826934814
164108 0.0009287893772125244
164109 0.0009151697158813477
164110 0.0011228322982788086
164111 0.001144707202911377
164112 0.0009582638740539551
164113 0.0009362697601318359
164114 0.0012634098529815674
164115 0.0009208917617797852
164116 0.0009151697158813477
164117 0.0010042190551757812
164118 0.0012451112270355225
164119 0.0009582638740539551
164120 0.0009210705757141113
164121 0.0010163187980651855
164122 0.0022738277912139893
164123 0.0009101927280426025
164124 0.0015410780

165106 0.0009224414825439453
165107 0.000937730073928833
165108 0.0013949275016784668
165109 0.0009532570838928223
165110 0.0009151697158813477
165111 0.0009208917617797852
165112 0.000912010669708252
165113 0.0009632706642150879
165114 0.0009532570838928223
165115 0.0009151697158813477
165116 0.0010124742984771729
165117 0.000912010669708252
165118 0.000957876443862915
165119 0.0009532570838928223
165120 0.0009152591228485107
165121 0.0010878443717956543
165122 0.0009267628192901611
165123 0.0009532570838928223
165124 0.0009151697158813477
165125 0.0009582638740539551
165126 0.0009267628192901611
165127 0.0009049177169799805
165128 0.0010042190551757812
165129 0.0009532570838928223
165130 0.0009532570838928223
165131 0.0009151697158813477
165132 0.0009208917617797852
165133 0.000912010669708252
165134 0.0009632706642150879
165135 0.0009532570838928223
165136 0.0009151697158813477
165137 0.0010124742984771729
165138 0.000912010669708252
165139 0.000957876443862915
165140 0.000928789377

166069 0.0009152591228485107
166070 0.001068413257598877
166071 0.0009686946868896484
166072 0.0009362697601318359
166073 0.0010001063346862793
166074 0.0009532570838928223
166075 0.0010879337787628174
166076 0.001149982213973999
166077 0.0009157061576843262
166078 0.0008993446826934814
166079 0.0008993446826934814
166080 0.0008993446826934814
166081 0.0008993446826934814
166082 0.0009532570838928223
166083 0.0009274482727050781
166084 0.001011669635772705
166085 0.0009267628192901611
166086 0.0009532570838928223
166087 0.00090751051902771
166088 0.001149982213973999
166089 0.0009192526340484619
166090 0.00090751051902771
166091 0.0010787546634674072
166092 0.0010249912738800049
166093 0.0009192526340484619
166094 0.00090751051902771
166095 0.0011110305786132812
166096 0.0010038018226623535
166097 0.0022738277912139893
166098 0.0010237395763397217
166099 0.0022738277912139893
166100 0.0010038018226623535
166101 0.0009381771087646484
166102 0.0008993446826934814
166103 0.000899344682693

In [123]:
pred = np.round(pre)
pred

array([0., 0., 0., ..., 0., 0., 0.])

In [71]:
y_test

[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,


In [124]:
# Accuracy, Precision, Recall, F1-Score
from sklearn.metrics import accuracy_score, recall_score, precision_score, f1_score

# score 출력
print('accuracy_score', float(accuracy_score(y_test, pred)))
print('recall_score', float(recall_score(y_test, pred)))
print('precision_score', float(precision_score(y_test, pred)))
print('f1_score', f1_score(y_test, pred))

# Confusion Matrix
from sklearn.metrics import confusion_matrix
print('\nconfusion_matrix\n', confusion_matrix(y_test, pred))

# ROC Curve
from sklearn.metrics import roc_auc_score
roc_auc = roc_auc_score(y_test, pred)
print('roc_curve 면적', roc_auc)

accuracy_score 0.9978234597370114
recall_score 0.0
precision_score 0.0
f1_score 0.0

confusion_matrix
 [[165957      0]
 [   362      0]]
roc_curve 면적 0.5
